In [1]:
import os, sys, re, io, math, time, folium, json, gzip
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from collections import *
from tqdm import *
from math import isnan, nan
from matplotlib.widgets import Slider
from glob import glob
from ipywidgets import *
from datetime import datetime, timedelta
from dateutil.tz import tzlocal
import ipywidgets as widgets
from IPython.display import *
from draw_util import *
from folium import plugins
display(HTML("<style>.container { width:100% !important; }</style>"))
pd.options.display.width = 1000
pd.options.display.max_columns = 1000
pd.options.display.max_rows = 100000
pd.options.display.float_format = '{0:f}'.format

# Disable scrolling for all output widgets
style = """
    <style>
       .jupyter-widgets-output-area .output_scroll {
            height: unset !important;
            border-radius: unset !important;
            -webkit-box-shadow: unset !important;
            box-shadow: unset !important;
        }
        .jupyter-widgets-output-area  {
            height: auto !important;
        }
    </style>
    """
display(HTML(style))

# disable autosave so that multiple user browser can attach the same notebook
%autosave 0


Autosave disabled


In [10]:
# Load SC data
df = pd.read_csv('./example/sc_data.csv.gz').set_index('t')
df.index = pd.DatetimeIndex(df.index)
sc_df = df.rename(columns={'postalcode': 'address'})

# Load dengue data
dengue_df = pd.read_csv('./example/dengue.csv.gz')

# Database search using Python JSON

In [12]:
# Load database in JSON format
import dbsearch
db_json = dbsearch.AddrDB('database.json.gz')

# address query in postal code format is much much faster
display(db_json[130017], db_json['130018'], db_json['1 Ghim Moh Rd'], db_json['1 GHIM MOH ROAD'])

[{'ADDRESS': ' 17 DOVER CRESCENT DOVER VILLE SINGAPORE 130017 ',
  'BLK_NO': '17',
  'BUILDING': 'DOVER VILLE',
  'LATITUDE': 1.307655,
  'LONGITUDE': 103.782891,
  'POSTAL': '130017',
  'ROAD_NAME': 'DOVER CRESCENT',
  'X': 22387.90339,
  'Y': 32219.36928}]

[{'ADDRESS': ' 18 DOVER CRESCENT DOVER VILLE SINGAPORE 130018 ',
  'BLK_NO': '18',
  'BUILDING': 'DOVER VILLE',
  'LATITUDE': 1.308083,
  'LONGITUDE': 103.783057,
  'POSTAL': '130018',
  'ROAD_NAME': 'DOVER CRESCENT',
  'X': 22406.37603,
  'Y': 32266.79431}]

[{'ADDRESS': ' 1 GHIM MOH ROAD GHIM MOH GREEN SINGAPORE 270001 ',
  'BLK_NO': '1',
  'BUILDING': 'GHIM MOH GREEN',
  'LATITUDE': 1.31288,
  'LONGITUDE': 103.786855,
  'POSTAL': '270001',
  'ROAD_NAME': 'GHIM MOH ROAD',
  'X': 22829.04815,
  'Y': 32797.13881}]

[{'ADDRESS': ' 1 GHIM MOH ROAD GHIM MOH GREEN SINGAPORE 270001 ',
  'BLK_NO': '1',
  'BUILDING': 'GHIM MOH GREEN',
  'LATITUDE': 1.31288,
  'LONGITUDE': 103.786855,
  'POSTAL': '270001',
  'ROAD_NAME': 'GHIM MOH ROAD',
  'X': 22829.04815,
  'Y': 32797.13881}]

In [4]:
display(dbp['6 KIM TIAN ROAD'])

[{'ADDRESS': ' 6 KIM TIAN ROAD HDB-BUKIT MERAH SINGAPORE 163006 ',
  'BLK_NO': '6',
  'BUILDING': 'HDB-BUKIT MERAH',
  'LATITUDE': 1.28401,
  'LONGITUDE': 103.827421,
  'POSTAL': '163006',
  'ROAD_NAME': 'KIM TIAN ROAD',
  'X': 27343.69511,
  'Y': 29604.78728},
 {'ADDRESS': ' 6 KIM TIAN ROAD KAI FOOK MANSION SINGAPORE 169246 ',
  'BLK_NO': '6',
  'BUILDING': 'KAI FOOK MANSION',
  'LATITUDE': 1.285144,
  'LONGITUDE': 103.82928,
  'POSTAL': '169246',
  'ROAD_NAME': 'KIM TIAN ROAD',
  'X': 27550.58195,
  'Y': 29730.24817}]

# Database search using Pandas DataFrame

In [15]:
# Load database in Pandas format
import dfsearch
db_pd = dfsearch.AddrDB('database.csv.gz')

display(dbp['6 KIM TIAN ROAD'], dbp[639549])

ADDRESS BLK_NO          BUILDING  LATITUDE  LONGITUDE  POSTAL      ROAD_NAME            X            Y
11961   6 KIM TIAN ROAD HDB-BUKIT MERAH SINGAPORE 163...      6   HDB-BUKIT MERAH  1.284010 103.827421  163006  KIM TIAN ROAD 27343.695110 29604.787280
12286   6 KIM TIAN ROAD KAI FOOK MANSION SINGAPORE 16...      6  KAI FOOK MANSION  1.285144 103.829280  169246  KIM TIAN ROAD 27550.581950 29730.248170

ADDRESS BLK_NO                                           BUILDING  LATITUDE  LONGITUDE  POSTAL      ROAD_NAME            X            Y
114533   41 STUDENTS WALK NANYANG TECHNOLOGICAL UNIVER...     41  NANYANG TECHNOLOGICAL UNIVERSITY (BLK 2) (HALL...  1.347880 103.685380  639549  STUDENTS WALK 11536.074980 36667.783570
114534   41 STUDENTS WALK NANYANG TECHNOLOGICAL UNIVER...     41  NANYANG TECHNOLOGICAL UNIVERSITY (BLK 10) (HAL...  1.348307 103.684015  639549  STUDENTS WALK 11384.120500 36714.929340
114535   41 STUDENTS WALK NANYANG TECHNOLOGICAL UNIVER...     41  NANYANG TECHNOLOGICAL UNIVERSITY (BLK 4) (HALL...  1.347812 103.684312  639549  STUDENTS WALK 11417.218970 36660.175830
114536   41 STUDENTS WALK NANYANG TECHNOLOGICAL UNIVER...     41  NANYANG TECHNOLOGICAL UNIVERSITY (BLK 1) (HALL...  1.347814 103.686160  639549  STUDENTS WALK 11622.866550 36660.445160
114537   41 STUDENTS WALK NANYANG TECHNOLOGICAL UNIVER...     41  NANYANG TECHNOLOGICAL UNIVERSITY (BLK 5) (HALL...  1.347723 103.684171  639549  STUDENTS WALK 11401.515240 36650.420430
114538   41 STUDENTS WALK NANYANG TECHNOLOGICAL UNIVER...     41  NANYANG TECHNOLOGICAL UNIVERSITY (BLK 7) (HALL...  1.348761 103.684554  639549  STUDENTS WALK 11444.172030 36765.116960
114539   41 STUDENTS WALK NANYANG TECHNOLOGICAL UNIVER...     41  NANYANG TECHNOLOGICAL UNIVERSITY (BLK 11) (HAL...  1.348154 103.683847  639549  STUDENTS WALK 11365.472280 36698.071500
114540   41 STUDENTS WALK NANYANG TECHNOLOGICAL UNIVER...     41  NANYANG TECHNOLOGICAL UNIVERSITY (BLK 3) (HALL...  1.347770 103.684705  639549  STUDENTS WALK 11460.978030 36655.575770
114541   41 STUDENTS WALK NANYANG TECHNOLOGICAL UNIVER...     41  NANYANG TECHNOLOGICAL UNIVERSITY (BLK 8) (HALL...  1.348611 103.684375  639549  STUDENTS WALK 11424.256000 36748.617850
114542   41 STUDENTS WALK NANYANG TECHNOLOGICAL UNIVER...     41  NANYANG TECHNOLOGICAL UNIVERSITY (BLK 9) (HALL...  1.348465 103.684201  639549  STUDENTS WALK 11404.863820 36732.377720

# Heatmap

In [6]:
my_map = folium.Map([1.34, 103.82], zoom_start = 12, control_scale=True, width='60%', height='60%',
                tiles = "https://maps-{s}.onemap.sg/v3/Default/{z}/{x}/{y}.png",
                attr = '<a href="http://SLA.gov.sg">Singapore Land Authority</a> &copy; All Rights Reserved!')
plot_data = {('red', 'Dengue'): dengue_df, (None, 'SC-usage'): sc_df}

showHeatmaps(plot_data, my_map, smooth=2)

# Countmap

In [17]:
my_map2 = folium.Map([1.34, 103.82], zoom_start = 12, control_scale=True, width='60%', height='60%',
                        tiles = "https://maps-{s}.onemap.sg/v3/Default/{z}/{x}/{y}.png",
                        attr = '<a href="http://SLA.gov.sg">Singapore Land Authority</a> &copy; All Rights Reserved!')
showCountmaps({'blue': dengue_df, 'red':sc_df['2020-6-1':'2020-6-3']}, my_map2, add_args=[['weight', 1], ['fill', True], ['fillOpacity', '10%']])